# Sparkify Project Workspace
This workspace contains a tiny subset (128MB) of the full dataset available (12GB). Feel free to use this workspace to build your project, or to explore a smaller subset with Spark before deploying your cluster on the cloud. Instructions for setting up your Spark cluster is included in the last lesson of the Extracurricular Spark Course content.

You can follow the steps below to guide your data analysis and model building portion of this project.

## Table of Contents

- [Load and Clean Dataset](#load)
- [Exploratory Data Analysis](#eda)
- [Feature Engineering](#f_eng)
- [Modelling](#model)
- [Conclusion](#conclusion)

In [1]:
%autosave 60
%config InlineBackend.figure_format = 'retina'
%matplotlib inline

# custom helper script
import helper as h

# standard libraries
from datetime import datetime as dt

# additional utilities
import numpy as np
import plotly.graph_objs as go
import plotly.offline as offline_py
offline_py.init_notebook_mode(connected=True)

# pyspark APIs
from pyspark.ml.classification import GBTClassifier, LogisticRegression, \
                                      RandomForestClassifier
from pyspark.ml.evaluation import MulticlassClassificationEvaluator
from pyspark.ml.feature import StandardScaler, VectorAssembler
from pyspark.ml.tuning import CrossValidator, ParamGridBuilder 
from pyspark.sql import SparkSession
from pyspark.sql.functions import avg, count, desc, isnan, udf
from pyspark.sql.functions import col as Fcol
from pyspark.sql.functions import max as Fmax
from pyspark.sql.functions import min as Fmin
from pyspark.sql.functions import round as Fround
from pyspark.sql.functions import sum as Fsum
from pyspark.sql.functions import when as Fwhen
from pyspark.sql.types import FloatType, IntegerType

Autosaving every 60 seconds


In [2]:
# create a Spark session
spark = SparkSession \
    .builder \
    .appName("sparkify") \
    .getOrCreate()

In [3]:
spark.sparkContext \
     .getConf() \
     .getAll()

[('spark.app.name', 'sparkify'),
 ('spark.app.id', 'local-1548348581951'),
 ('spark.rdd.compress', 'True'),
 ('spark.serializer.objectStreamReset', '100'),
 ('spark.master', 'local[*]'),
 ('spark.driver.port', '49424'),
 ('spark.executor.id', 'driver'),
 ('spark.submit.deployMode', 'client'),
 ('spark.ui.showConsoleProgress', 'true'),
 ('spark.driver.host', 'o.local')]

<a id="load"></a>

# Load and Clean Dataset

Clean your dataset, checking for invalid or missing data. For example, records without userids or sessionids. In this workspace, the filename is `mini_sparkify_event_data.json`.

In [4]:
event_data = "data/mini_sparkify_event_data.json"
df = spark.read.json(event_data)

h.spark_shape(df)

(286500, 18)

In [5]:
df.persist()

DataFrame[artist: string, auth: string, firstName: string, gender: string, itemInSession: bigint, lastName: string, length: double, level: string, location: string, method: string, page: string, registration: bigint, sessionId: bigint, song: string, status: bigint, ts: bigint, userAgent: string, userId: string]

### Data cleaning

First checking number of null values in each column:

In [6]:
nan_cols = []       # this will contain columns that have any number of null values
nan_cols_less = []  # contains column names which have 8346 nans
nan_cols_more = []  # contains column names which have 58392 nans

# NOTE:
# nan_cols_less + nan_cols_more = nan_cols

for col in df.columns:

    # count number of nans
    nan_count = df.where(df[col].isNull()).select(col).count()
    
    # columns with 8346 nans
    if nan_count==8346:
        nan_cols.append(col)         # add to columns' list with non-zero nans
        nan_cols_less.append(col)    # add to columns' list with 8346 nans
        print("Column name: {0}, Number of nans: {1}"\
                .format(col,nan_count))
    
    # columns with 58392 nans
    elif nan_count==58392:
        nan_cols.append(col)         # add to columns' list with non-zero nans
        nan_cols_more.append(col)    # add to column' list with 58392 nans
        print("Column name: {0}, Number of nans: {1}"\
                .format(col,nan_count))

Column name: artist, Number of nans: 58392
Column name: firstName, Number of nans: 8346
Column name: gender, Number of nans: 8346
Column name: lastName, Number of nans: 8346
Column name: length, Number of nans: 58392
Column name: location, Number of nans: 8346
Column name: registration, Number of nans: 8346
Column name: song, Number of nans: 58392
Column name: userAgent, Number of nans: 8346


### Observation

Two different levels of null values are here: 8346 and 58392, 8346 is just **2%** of our data, so we **can drop** the rows which have null values for columns with 8346 nans.

58392 is **20%** of the data, so we need to study more about these features. Let's study this case for one of these columns( `Song` column) and see whether they are related:

In [7]:
df.where(df.page != "NextSong").select("Song").show()

+----+
|Song|
+----+
|null|
|null|
|null|
|null|
|null|
|null|
|null|
|null|
|null|
|null|
|null|
|null|
|null|
|null|
|null|
|null|
|null|
|null|
|null|
|null|
+----+
only showing top 20 rows



Whenever user did not click on _NextSong_, the value in `Song` column is null. It is not missing data or error in data entry. It is just that song was not changed, so the log report is displaying null.

Similar might be the case for other columns with this much  `nan`s. For safety purpose, we will not drop `nan`s from the following columns:

In [8]:
# show the columns
for col in df.columns:
    nan_count = df.where(df[col].isNull()).select(col).count()
    if nan_count == 58392:
        print(col)

artist
length
song


From the above output, it is very clear that these three features are dependent on one another. Typical dependence can be like this:

$$ No\ Artist \implies No\ Song $$

$$ No\ Song \implies No\ Song\ Length $$

This is my opinion on how this dependency could look like. Feel free to share yours.

This relation confirms our decision of not dropping these features together.

Now let's see if other columns (with 8346 nans) have same relation too.

In [9]:
df_null_8346 = df.where(df.firstName.isNull()).select(nan_cols_less)
df_null_8346.show()

+---------+------+--------+--------+------------+---------+
|firstName|gender|lastName|location|registration|userAgent|
+---------+------+--------+--------+------------+---------+
|     null|  null|    null|    null|        null|     null|
|     null|  null|    null|    null|        null|     null|
|     null|  null|    null|    null|        null|     null|
|     null|  null|    null|    null|        null|     null|
|     null|  null|    null|    null|        null|     null|
|     null|  null|    null|    null|        null|     null|
|     null|  null|    null|    null|        null|     null|
|     null|  null|    null|    null|        null|     null|
|     null|  null|    null|    null|        null|     null|
|     null|  null|    null|    null|        null|     null|
|     null|  null|    null|    null|        null|     null|
|     null|  null|    null|    null|        null|     null|
|     null|  null|    null|    null|        null|     null|
|     null|  null|    null|    null|    

In [10]:
h.spark_shape(df_null_8346)

(8346, 6)

Only showing top 20 rows, you can check it for other rows also. All are null values.

Dropping null values:

In [11]:
df_final = df.where(df.firstName.isNotNull())

<a  id="nrows_df"></a>

Testing

In [12]:
h.spark_shape(df_final)

(278154, 18)

<a id="eda"></a>

## Exploratory Data Analysis
When you're working with the full dataset, perform EDA by loading a small subset of the data and doing basic manipulations within Spark. In this workspace, you are already provided a small subset of data you can explore.

### Define Churn

Once you've done some preliminary analysis, create a column `Churn` to use as the label for your model. I suggest using the `Cancellation Confirmation` events to define your churn, which happen for both paid and free users. As a bonus task, you can also look into the `Downgrade` events.

### Explore Data
Once you've defined churn, perform some exploratory data analysis to observe the behavior for users who stayed vs users who churned. You can start by exploring aggregates on these two groups of users, observing how much of a specific action they experienced per a certain time unit or number of songs played.

#### 1. Pages Distribution

In [13]:
page_nuniq = df_final.select("page").distinct().count()
page_nuniq

19

In [14]:
page_nuniq_before = df.select("page").distinct().count()
page_nuniq_before

22

Seems like we dropped some classes in `page` column while handling `nan`s. Let's see what are those.

In [15]:
pages_before = [log["page"] for log in df.select("page")\
                              .distinct()\
                              .collect()]
pages_after = [log["page"] for log in df_final.select("page")\
                             .distinct()\
                             .collect()]

removed_pages = [page_class\
                 for page_class in pages_before\
                 if page_class not in pages_after]

removed_pages

['Submit Registration', 'Login', 'Register']

<a id='issue1'></a>

I am unable to judge importance of these classess. We will drop them for now.

View:

In [16]:
df_final.select("page").distinct().take(page_nuniq)

[Row(page='Cancel'),
 Row(page='Submit Downgrade'),
 Row(page='Thumbs Down'),
 Row(page='Home'),
 Row(page='Downgrade'),
 Row(page='Roll Advert'),
 Row(page='Logout'),
 Row(page='Save Settings'),
 Row(page='Cancellation Confirmation'),
 Row(page='About'),
 Row(page='Settings'),
 Row(page='Add to Playlist'),
 Row(page='Add Friend'),
 Row(page='NextSong'),
 Row(page='Thumbs Up'),
 Row(page='Help'),
 Row(page='Upgrade'),
 Row(page='Error'),
 Row(page='Submit Upgrade')]

In [17]:
pages_pd = df_final.select("page") \
                   .groupBy("page") \
                   .count() \
                   .orderBy("count") \
                   .toPandas()
pages_pd.head()

page  count
0                     Cancel     52
1  Cancellation Confirmation     52
2           Submit Downgrade     63
3             Submit Upgrade    159
4                      Error    252

<a id="nextsong_outlier"></a>

In [18]:
h.page_dist(pages_pd)

Let's see why this graph is **left-skewed.**

In [19]:
df_pages = df_final.select("page").groupBy("page").count().orderBy(desc("count"))
df_pages.agg(Fsum("count")) \
        .collect()

[Row(sum(count)=278154)]

In [20]:
pages_tot_cnt = df_pages.agg(Fsum("count")) \
                        .collect()[0][0]
print("The total # of page views are: {0}".format(pages_tot_cnt))

The total # of page views are: 278154


This is same as the number of rows in [`df_final`](#nrows_df).

In [21]:
# creating lambda function to see count as percentage
get_percent = udf(lambda page_count: 100 * page_count/pages_tot_cnt, FloatType())
df_pages = df_pages.withColumn("percentage", get_percent(df_pages["count"]))
df_pages.show(5)

+---------------+------+----------+
|           page| count|percentage|
+---------------+------+----------+
|       NextSong|228108| 82.007805|
|      Thumbs Up| 12551| 4.5122485|
|           Home| 10082|  3.624611|
|Add to Playlist|  6526| 2.3461823|
|     Add Friend|  4277| 1.5376375|
+---------------+------+----------+
only showing top 5 rows



`NextSong` covers a large portion of our observations.

Let's filter `NextSong` class and see again.

In [22]:
h.page_dist_2(pages_pd)

Cancellations are less in number. That is what we have to predict. We have to choose the metric accordingly. This chart shows the most cmommon actions taken by users, like liking a song, adding to playlist, visiting home page and adding friend.

#### 2. Number of users who did cancellation confirmation.

In [23]:
tot_user_cnt = df_final.select("userId").distinct().count()
print("Total users are: {0}".format(tot_user_cnt))

Total users are: 225


In [24]:
c_user_cnt = df_final.where(df_final.page =="Cancellation Confirmation") \
                     .select("userId").distinct().count()
print("{0} users out of {1} are at risk to churn." \
      .format(c_user_cnt, tot_user_cnt))
percent = 100 * c_user_cnt / tot_user_cnt
print("That is {0}%".format(round(percent, 2)))

52 users out of 225 are at risk to churn.
That is 23.11%


View:

In [25]:
df_final.where(df_final.page =="Cancellation Confirmation") \
        .select("userId") \
        .distinct() \
        .show(c_user_cnt)

+------+
|userId|
+------+
|   125|
|    51|
|    54|
|100014|
|   101|
|    29|
|100021|
|    87|
|    73|
|     3|
|    28|
|100022|
|100025|
|300007|
|100006|
|    18|
|    70|
|100005|
|    17|
|100007|
|300001|
|100009|
|100015|
|200024|
|100003|
|   103|
|100024|
|    53|
|   122|
|200017|
|    58|
|100011|
|100019|
|100012|
|200018|
|200016|
|200020|
|   106|
|   143|
|    32|
|200001|
|   105|
|200011|
|100023|
|100013|
|100017|
|   121|
|    12|
|200015|
|   129|
|200021|
|100001|
+------+



#### 3. Correcting data type of `ts` column

In [26]:
df_final.select(["ts"]).show(5)

+-------------+
|           ts|
+-------------+
|1538352117000|
|1538352180000|
|1538352394000|
|1538352416000|
|1538352676000|
+-------------+
only showing top 5 rows



Creating new columns `time` with `datetime.datetime` class.

In [27]:
ts_to_dt = udf(lambda x: dt.fromtimestamp(x / 1000) \
               .strftime("%Y-%m-%d %H:%M:%S"))
df_final = df_final.withColumn("time", ts_to_dt(df_final.ts))

View:

In [28]:
df_final.select(["time"]).show(5)

+-------------------+
|               time|
+-------------------+
|2018-10-01 05:31:57|
|2018-10-01 05:33:00|
|2018-10-01 05:36:34|
|2018-10-01 05:36:56|
|2018-10-01 05:41:16|
+-------------------+
only showing top 5 rows



#### 4. Create `isChurn` column:

In [29]:
df_c = df_final.where(df_final.page == "Cancellation Confirmation") \
               .select("userId") \
               .distinct()

In [30]:
ids_c = [user_log['userId'] for user_log in df_c.collect()]

In [31]:
ids_c

['125',
 '51',
 '54',
 '100014',
 '101',
 '29',
 '100021',
 '87',
 '73',
 '3',
 '28',
 '100022',
 '100025',
 '300007',
 '100006',
 '18',
 '70',
 '100005',
 '17',
 '100007',
 '300001',
 '100009',
 '100015',
 '200024',
 '100003',
 '103',
 '100024',
 '53',
 '122',
 '200017',
 '58',
 '100011',
 '100019',
 '100012',
 '200018',
 '200016',
 '200020',
 '106',
 '143',
 '32',
 '200001',
 '105',
 '200011',
 '100023',
 '100013',
 '100017',
 '121',
 '12',
 '200015',
 '129',
 '200021',
 '100001']

In [32]:
df_c = df_final.withColumn("isChurn", df_final.userId.isin(ids_c))

In [33]:
df_c.persist()

DataFrame[artist: string, auth: string, firstName: string, gender: string, itemInSession: bigint, lastName: string, length: double, level: string, location: string, method: string, page: string, registration: bigint, sessionId: bigint, song: string, status: bigint, ts: bigint, userAgent: string, userId: string, time: string, isChurn: boolean]

#### 5. Gender distribution between churn and non-churn users

In [34]:
gender_pd = df_c.dropDuplicates(["userId", "gender"]) \
                .groupby(["isChurn", "gender"]) \
                .count() \
                .orderBy("isChurn", "gender") \
                .toPandas()

In [35]:
gender_pd.head()

isChurn gender  count
0    False      F     84
1    False      M     89
2     True      F     20
3     True      M     32

In [36]:
h.gender_dist(gender_pd)

Overall male listeners are more.

#### 6. Pages distribution based on churn

To avoid skewed distribution as faced [here](#nextsong_outlier), we will not include `NextSong` column.

In [37]:
c_cnt = df_c.filter(df_c.isChurn).count()
nc_cnt = df_c.filter(~df_c.isChurn).count()

c_temp = df_c.filter((df_c.isChurn) & (df_c.page!="NextSong")) \
             .groupby(["page"]) \
             .count()
c_temp = c_temp.withColumn("pCount", 100 * c_temp["count"]/c_cnt) \
               .sort("page")

nc_temp = df_c.filter((~df_c.isChurn) & (df_c.page!="NextSong")) \
              .groupby(["page"]) \
              .count()
nc_temp = nc_temp.withColumn("pCount", 100 * nc_temp["count"]/nc_cnt) \
                 .sort("page")

In [38]:
c_temp_pd = c_temp.toPandas()
nc_temp_pd = nc_temp.toPandas()

In [39]:
c_temp.show(5)

+--------------------+-----+-------------------+
|                page|count|             pCount|
+--------------------+-----+-------------------+
|               About|   56|0.12482168330955777|
|          Add Friend|  636|  1.417617689015692|
|     Add to Playlist| 1038| 2.3136590584878745|
|              Cancel|   52| 0.1159058487874465|
|Cancellation Conf...|   52| 0.1159058487874465|
+--------------------+-----+-------------------+
only showing top 5 rows



In [40]:
c_temp_pd.shape

(18, 3)

In [41]:
h.page_dist_3(c_temp_pd, nc_temp_pd)

Some actions that are more frequent are:

- Add friend: Adding a friend on the platform
- Add to Playlist: Adding a song to one's playlist
- Home: Home page of Sparkify
- Thumbs Up: Liking a song
- Roll Advert: Skipping ads

#### 7. Distribution of level for churned users

In [42]:
level_pd = df_c.filter(df_c.isChurn).select("level").toPandas()
level_pd.head()

level
0  paid
1  paid
2  paid
3  paid
4  paid

In [43]:
h.plot_levels(level_pd)

$70\%$ of churned users are paying customers. Customer retention is relatively more important for paid ones because they are directly connected with the revenue of the company.

#### 8. Time distribution based on churn

##### Based on hour level

In [44]:
# create hour column
get_hr = udf(lambda x: dt.fromtimestamp(x/1000).hour, IntegerType())
df_c = df_c.withColumn("hour", get_hr(df_c.ts))

# get day of week(with 0 as Monday)
get_dow = udf(lambda x: dt.fromtimestamp(x/1000).weekday(), IntegerType())
df_c = df_c.withColumn("dow", get_dow(df_c.ts))

# get day of month
get_dom = udf(lambda x: dt.fromtimestamp(x/1000).day, IntegerType())
df_c = df_c.withColumn("dom", get_dom(df_c.ts))

In [45]:
c_hod = df_c.filter((df_c.isChurn) & (df_c.page == "NextSong")) \
            .select("hour") \
            .groupby("hour") \
            .count() \
            .orderBy("hour") \
            .toPandas()

nc_hod = df_c.filter((~df_c.isChurn) & (df_c.page == "NextSong")) \
            .select("hour") \
            .groupby("hour") \
            .count() \
            .orderBy("hour") \
            .toPandas()

c_hod.head()

hour  count
0     0   1918
1     1   1757
2     2   1702
3     3   1595
4     4   1568

In [46]:
h.plot_hod(c_hod, nc_hod)

From above graph we can see that non-churn user are more active during day-time. Lets see this comparison in more detail.

In [47]:
h.plot_diff_hod(c_hod, nc_hod)

Non-churn users activity during day-time is more clear now.

##### Based on day-of-week level

In [48]:
c_dow = df_c.filter((df_c.isChurn) & (df_c.page == "NextSong")) \
            .select("dow") \
            .groupby("dow") \
            .count() \
            .toPandas()

nc_dow = df_c.filter((~df_c.isChurn) & (df_c.page == "NextSong")) \
             .select("dow") \
             .groupby("dow") \
             .count() \
             .toPandas()

c_dow.head()

dow  count
0    1   5928
1    6   2066
2    3   6133
3    5   4704
4    4   6654

In [49]:
h.plot_dow(c_dow, nc_dow)

Activity is more on weekdays.

##### Based on day level

In [50]:
c_dom = df_c.filter((df_c.isChurn) & (df_c.page == "NextSong")) \
            .select("dom") \
            .groupby("dom") \
            .count() \
            .toPandas()

nc_dom = df_c.filter((~df_c.isChurn) & (df_c.page == "NextSong")) \
             .select("dom") \
             .groupby("dom") \
             .count() \
             .toPandas()

c_dom.head()

dom  count
0   31   1041
1   28     80
2   26    528
3   27    584
4   12   2174

In [51]:
h.plot_dom(c_dom, nc_dom)

An interesting pattern is seen here. Let's visualize it in more detail.

In [52]:
h.plot_diff_dom(c_dom, nc_dom)

Non-churn users are generally less active in the start of the month as compared to churn users, and opposite is the case at the EOM.

#### 9. userAgent

In [53]:
df_c.select("userAgent") \
    .distinct() \
    .toPandas()['userAgent'][0]

'"Mozilla/5.0 (Macintosh; Intel Mac OS X 10_8_5) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/36.0.1985.143 Safari/537.36"'

`userAgent` is also not a useful feature. In above output, we cannot conclude about the specifications of device. Chrome and Safari both are present. It creates confusion.

#### 10. Status

In [54]:
df_c.select("status").groupby("status").count().show()

+------+------+
|status| count|
+------+------+
|   307| 23184|
|   404|   252|
|   200|254718|
+------+------+



`status` doesn't look like a useful columns here. It just shows the HTTP status code.

#### 11. Song

In [55]:
df_c.select("song").groupby("song").count().count()

58481

`Song` also has so many levels. Obviously, classifying churn based on every song can be very challenging. We will use it for aggregation, like songs per session or songs per user.

#### 12. Method

In [56]:
df_c.select("method").distinct().show()

+------+
|method|
+------+
|   PUT|
|   GET|
+------+



`method` also doesn't look like a useful column. These are just HTTP methods for REST APIs.

#### 13. Location

In [57]:
df_c.select("location").distinct().collect()

[Row(location='Gainesville, FL'),
 Row(location='Atlantic City-Hammonton, NJ'),
 Row(location='Deltona-Daytona Beach-Ormond Beach, FL'),
 Row(location='San Diego-Carlsbad, CA'),
 Row(location='Cleveland-Elyria, OH'),
 Row(location='Kingsport-Bristol-Bristol, TN-VA'),
 Row(location='New Haven-Milford, CT'),
 Row(location='Birmingham-Hoover, AL'),
 Row(location='Corpus Christi, TX'),
 Row(location='Dubuque, IA'),
 Row(location='Las Vegas-Henderson-Paradise, NV'),
 Row(location='Indianapolis-Carmel-Anderson, IN'),
 Row(location='Seattle-Tacoma-Bellevue, WA'),
 Row(location='Albany, OR'),
 Row(location='Winston-Salem, NC'),
 Row(location='Bakersfield, CA'),
 Row(location='Los Angeles-Long Beach-Anaheim, CA'),
 Row(location='Minneapolis-St. Paul-Bloomington, MN-WI'),
 Row(location='San Francisco-Oakland-Hayward, CA'),
 Row(location='Phoenix-Mesa-Scottsdale, AZ'),
 Row(location='Allentown-Bethlehem-Easton, PA-NJ'),
 Row(location='Miami-Fort Lauderdale-West Palm Beach, FL'),
 Row(location='Se

We can do some feature engineering in upcoming sections to target churned users based on location.

#### 14. Length

In [58]:
df_c.select(Fround("length", 0).alias("lengthInSec")) \
    .distinct() \
    .show()

+-----------+
|lengthInSec|
+-----------+
|      299.0|
|      305.0|
|      496.0|
|      692.0|
|      596.0|
|      558.0|
|      769.0|
|      147.0|
|      184.0|
|      170.0|
|      576.0|
|      782.0|
|      810.0|
|      720.0|
|      169.0|
|      160.0|
|      735.0|
|      608.0|
|       70.0|
|      311.0|
+-----------+
only showing top 20 rows



In [59]:
df_c.select(Fround("length", 0).alias("lengthInSec")) \
    .distinct() \
    .count()

909

Song length also looks like a less important feature. We will use it for aggregation in feature engineering section.

I am **not considering** distributions of firstname and lastname by churn count.

#### 15. Auth

In [60]:
df_c.select("auth").distinct().show()

+---------+
|     auth|
+---------+
|Cancelled|
|Logged In|
+---------+



In [61]:
df_c.filter(df_c.isChurn) \
    .select("auth") \
    .groupBy("auth") \
    .count() \
    .show()

+---------+-----+
|     auth|count|
+---------+-----+
|Cancelled|   52|
|Logged In|44812|
+---------+-----+



In [62]:
df_c.filter(~df_c.isChurn) \
    .select("auth") \
    .groupBy("auth") \
    .count() \
    .show()

+---------+------+
|     auth| count|
+---------+------+
|Logged In|233290|
+---------+------+



Noting can be concluded from the above results for authentication column. We could use this to see the session duration but that's available from `sessionID` column.

#### 16. itemInSession

In [63]:
df_c.select("itemInSession").distinct().count()

1311

$1311$ categories are very large to consider. We will drop them in further analysis.

Let's see whether song length has some interesting distribution.

#### 17. Song length

In [64]:
df_pd = df_c.toPandas()

In [65]:
df_pd.head()

artist       auth firstName gender  itemInSession lastName  \
0    Martha Tilston  Logged In     Colin      M             50  Freeman   
1  Five Iron Frenzy  Logged In     Micah      M             79     Long   
2      Adam Lambert  Logged In     Colin      M             51  Freeman   
3            Enigma  Logged In     Micah      M             80     Long   
4         Daft Punk  Logged In     Colin      M             52  Freeman   

      length level                        location method ...   \
0  277.89016  paid                 Bakersfield, CA    PUT ...    
1  236.09424  free  Boston-Cambridge-Newton, MA-NH    PUT ...    
2  282.82730  paid                 Bakersfield, CA    PUT ...    
3  262.71302  free  Boston-Cambridge-Newton, MA-NH    PUT ...    
4  223.60771  paid                 Bakersfield, CA    PUT ...    

                            song  status             ts  \
0                      Rockpools     200  1538352117000   
1                         Canada     200  1538352180000   
2              Time For Miracles     200  1538352394000   
3    Knocking On Forbidden Doors     200  1538352416000   
4  Harder Better Faster Stronger     200  1538352676000   

                                           userAgent  userId  \
0  Mozilla/5.0 (Windows NT 6.1; WOW64; rv:31.0) G...      30   
1  "Mozilla/5.0 (Windows NT 6.1; WOW64) AppleWebK...       9   
2  Mozilla/5.0 (Windows NT 6.1; WOW64; rv:31.0) G...      30   
3  "Mozilla/5.0 (Windows NT 6.1; WOW64) AppleWebK...       9   
4  Mozilla/5.0 (Windows NT 6.1; WOW64; rv:31.0) G...      30   

                  time isChurn hour dow  dom  
0  2018-10-01 05:31:57   False    5   0    1  
1  2018-10-01 05:33:00   False    5   0    1  
2  2018-10-01 05:36:34   False    5   0    1  
3  2018-10-01 05:36:56   False    5   0    1  
4  2018-10-01 05:41:16   False    5   0    1  

[5 rows x 23 columns]

In [66]:
h.plot_song_len(df_pd)

No trend can be seen from here. Seems like most songs are $4\ minutes$ in length.

#### 18. Device

Let's see which device the user is using.

In [67]:
# get device from userAgent column
get_device = udf(lambda userAgent: userAgent.split("(")[1] \
                 .split(";")[0] \
                 .split(" ")[0])

df_c = df_c.withColumn("device", get_device(df_c.userAgent))

df_c.select("device") \
    .distinct() \
    .show()

+----------+
|    device|
+----------+
|      iPad|
|       X11|
|    iPhone|
| Macintosh|
|compatible|
|   Windows|
+----------+



In [68]:
# checking what "compatible" stands for
for log in df_c.select("userAgent").collect():
    if log["userAgent"].split("(")[1] \
                       .split(";")[0] \
                       .split(" ")[0] == "compatible": # do string split to check for device type
        print(log["userAgent"])
        break

Mozilla/5.0 (compatible; MSIE 10.0; Windows NT 6.1; WOW64; Trident/6.0)


In [69]:
# checking what "X11" stands for
for log in df_c.select("userAgent").collect():
    if log["userAgent"].split("(")[1] \
                       .split(";")[0] \
                       .split(" ")[0] == "X11": # do string split to check for device type
        print(log["userAgent"])
        break

Mozilla/5.0 (X11; Linux x86_64; rv:31.0) Gecko/20100101 Firefox/31.0


Based on information about `compatible` and `X11`, it looks like `compatibele` is for Windows devices and `X11` is for Linux.

We will use this to further decrease the number of levels in `userAgent` column.

In [70]:
df_c = df_c.replace(["X11", "compatible"], ["Linux", "Windows"], "device")

df_c.select("device") \
    .distinct() \
    .show()

+---------+
|   device|
+---------+
|     iPad|
|   iPhone|
|Macintosh|
|    Linux|
|  Windows|
+---------+



In [71]:
# converting to Pandas dataframe for plotting
device_pd = df_c.select("device") \
                .groupby("device") \
                .count() \
                .orderBy("device") \
                .toPandas()

device_pd.head()

device   count
0      Linux    8961
1  Macintosh  102749
2    Windows  143871
3       iPad   11381
4     iPhone   11192

In [72]:
h.plot_devices(device_pd)

Looks like what we've expected. **Windows** is the most popular OS. Nothing new from this graph.

<a id="f_eng"></a>

## Feature Engineering
Once you've familiarized yourself with the data, build out the features you find promising to train your model on. To work with the full dataset, you can follow the following steps.
- Write a script to extract the necessary features from the smaller subset of data
- Ensure that your script is scalable, using the best practices discussed in Lesson 3
- Try your script on the full data set, debugging your script if necessary

If you are working in the classroom workspace, you can just extract features based on the small subset of data contained here. Be sure to transfer over this work to the larger dataset when you work on your Spark cluster.

Features to create ( based on each user )

1. Gender
2. Songs per user
3. Sessions per user
4. Number of songs per session
5. Average time per session
6. Level of user
7. Proportion of page visits
8. Number of artists user has listened to
9. Region based on midwest, northeast, south and west

### 1. Gender

In [73]:
# extracting only gender
gender_df = df_c.select(["userId", "gender"]) \
                .dropDuplicates()

In [74]:
# creating dummy columns for gender variable
# create map
genders = gender_df.select("gender") \
                   .distinct() \
                   .rdd \
                   .flatMap(lambda x: x) \
                   .collect()

# add naming pattern
genders_expr = [Fwhen(Fcol("gender") == g, 1) \
                 .otherwise(0) \
                 .alias("gender" + g.capitalize()) \
                for g in genders]

gender_df = gender_df.select("userId", "gender", *genders_expr) \
                     .drop("gender") \
                     .orderBy("userId")

gender_df.show(5)

+------+-------+-------+
|userId|genderF|genderM|
+------+-------+-------+
|    10|      0|      1|
|   100|      0|      1|
|100001|      1|      0|
|100002|      1|      0|
|100003|      1|      0|
+------+-------+-------+
only showing top 5 rows



In [75]:
h.spark_shape(gender_df)

(225, 3)

### 2. Songs per user

In [76]:
song_df = df_c.filter(df_c.page == "NextSong") \
              .select(["userId"]) \
              .dropDuplicates() \
              .groupby("userID") \
              .count()

song_df = song_df.withColumnRenamed("count", "songCount") \
                 .orderBy("userId")

song_df.show(5)

+------+---------+
|userID|songCount|
+------+---------+
|    10|        1|
|   100|        1|
|100001|        1|
|100002|        1|
|100003|        1|
+------+---------+
only showing top 5 rows



In [77]:
h.spark_shape(song_df)

(225, 2)

### 3. Sessions per user

In [78]:
session_df = df_c.select(["userId", "sessionId"]) \
                 .dropDuplicates() \
                 .groupby("userId") \
                 .count()

session_df = session_df.withColumnRenamed("count", "sessionCount") \
                       .orderBy("userId")

session_df.show(5)

+------+------------+
|userId|sessionCount|
+------+------------+
|    10|           6|
|   100|          35|
|100001|           4|
|100002|           4|
|100003|           2|
+------+------------+
only showing top 5 rows



In [79]:
h.spark_shape(session_df)

(225, 2)

### 4. Songs per session

In [80]:
avg_songs_per_session_df = df_c.filter(df_c.page =="NextSong") \
                               .groupBy(["userId", "sessionId"]) \
                               .count()

avg_songs_per_session_df = avg_songs_per_session_df.groupby("userId") \
                          .agg(avg(avg_songs_per_session_df["count"]) \
                          .alias("avgSongsPerSession")) \
                          .orderBy("userId")

avg_songs_per_session_df.show(5)

+------+------------------+
|userId|avgSongsPerSession|
+------+------------------+
|    10|112.16666666666667|
|   100| 78.88235294117646|
|100001|             33.25|
|100002|             48.75|
|100003|              25.5|
+------+------------------+
only showing top 5 rows



In [81]:
h.spark_shape(avg_songs_per_session_df)

(225, 2)

### 5. Average time per session

In [82]:
avg_time_per_session_df = df_c.groupby("userId", "sessionId") \
                              .agg(((Fmax(df_c.ts)-Fmin(df_c.ts))/(1000*60)) \
                              .alias("sessionDurationMinutes"))

In [83]:
avg_time_per_session_df.show(5)

+------+---------+----------------------+
|userId|sessionId|sessionDurationMinutes|
+------+---------+----------------------+
|    92|      358|    257.31666666666666|
|    42|      433|     74.73333333333333|
|   101|      635|     3300.016666666667|
|   120|      627|     951.3333333333334|
|   140|      798|     9.616666666666667|
+------+---------+----------------------+
only showing top 5 rows



In [84]:
avg_time_per_session_df = avg_time_per_session_df.groupby("userId") \
                                       .agg(avg(avg_time_per_session_df. \
                                                sessionDurationMinutes) \
                                       .alias("avgSessionDurationMinutes")) \
                                       .sort("userId")

avg_time_per_session_df.show(5)

+------+-------------------------+
|userId|avgSessionDurationMinutes|
+------+-------------------------+
|    10|       459.74722222222226|
|   100|        316.5190476190476|
|100001|       148.15833333333333|
|100002|       201.18333333333334|
|100003|        99.11666666666667|
+------+-------------------------+
only showing top 5 rows



In [85]:
h.spark_shape(avg_time_per_session_df)

(225, 2)

### 6. Latest financial status of user: Paid or free

In [86]:
level_df = df_c.groupby("userId", "level") \
                .agg(Fmax(df_c.ts).alias("finalTime")) \
                .sort("userId")

level_df.show(5)

+------+-----+-------------+
|userId|level|    finalTime|
+------+-----+-------------+
|    10| paid|1542631788000|
|   100| paid|1543587349000|
|   100| free|1542215545000|
|100001| free|1538498205000|
|100002| paid|1543799476000|
+------+-----+-------------+
only showing top 5 rows



In [87]:
recent_level_ts_df = level_df.groupby("userId") \
                        .agg(Fmax(level_df.finalTime).alias("recent"))

recent_level_ts_df.show(5)

+------+-------------+
|userId|       recent|
+------+-------------+
|    10|1542631788000|
|   100|1543587349000|
|100001|1538498205000|
|100002|1543799476000|
|100003|1539274781000|
+------+-------------+
only showing top 5 rows



In [88]:
recent_level_df = recent_level_ts_df.join(level_df, \
                          [level_df.userId == recent_level_ts_df.userId, \
                           recent_level_ts_df.recent == level_df.finalTime]) \
                          .select(level_df.userId, "level") \
                          .sort("userId")

recent_level_df.show(5)

+------+-----+
|userId|level|
+------+-----+
|    10| paid|
|   100| paid|
|100001| free|
|100002| paid|
|100003| free|
+------+-----+
only showing top 5 rows



In [89]:
levels = recent_level_df.select("level") \
                        .distinct() \
                        .rdd \
                        .flatMap(lambda x: x) \
                        .collect()

levels_expr = [Fwhen(Fcol("level") == l, 1).otherwise(0) \
                .alias("level" + l.capitalize()) \
                for l in levels]

recent_level_df = recent_level_df.select("userId", "level", *levels_expr) \
                                 .drop("level") \
                                 .orderBy("userId")

recent_level_df.show(5)

+------+---------+---------+
|userId|levelFree|levelPaid|
+------+---------+---------+
|    10|        0|        1|
|   100|        0|        1|
|100001|        1|        0|
|100002|        0|        1|
|100003|        1|        0|
+------+---------+---------+
only showing top 5 rows



In [90]:
h.spark_shape(recent_level_df)

(225, 3)

### 7. Proportion of page visits

In [91]:
# all pages
pages = [(row['page']) \
         for row in df_c.select("page").dropDuplicates().collect()]

# must remove the lookahead bias
pages.remove("Cancel")
pages.remove("Cancellation Confirmation")

# calculate the total pages each user viewed
user_page_view_count = df_c.groupby("userId") \
                           .count() \
                           .orderBy("userId")

user_page_view_count = user_page_view_count.withColumnRenamed("count", \
                                                              "pageCount")


for page in pages:
    # remove the space in column names
    col_name = "count" + page.replace(" ", "")
    # calculate count of page type by userId
    view_count = df_c.filter(df_c.page==page) \
                     .groupby("userId") \
                     .count()
    # rename the columns of view_count temporarily
    view_count = view_count.withColumnRenamed("count", col_name) \
                           .withColumnRenamed("userId", "userIdTemp")
    
    # merge it with user_page_view_count
    user_page_view_count = user_page_view_count \
                          .join(view_count, \
                                user_page_view_count.userId == \
                                view_count.userIdTemp, "left") \
                          .drop("userIdTemp")

# sort user_page_viee_count by userId
user_page_view_count = user_page_view_count.sort("userId")

# null value means no views, So replacing them with 0
user_page_view_count = user_page_view_count.fillna(0)

In [92]:
pd_temp = user_page_view_count.toPandas()
pd_temp.head()

userId  pageCount  countSubmitDowngrade  countThumbsDown  countHome  \
0      10        795                     0                4         30   
1     100       3214                     1               27        105   
2  100001        187                     0                2         11   
3  100002        218                     0                0          6   
4  100003         78                     0                0          7   

   countDowngrade  countRollAdvert  countLogout  countSaveSettings  \
0               7                1           11                  1   
1              30               25           35                  5   
2               0               14            7                  0   
3               2                3            1                  0   
4               0                9            3                  0   

   countAbout  countSettings  countAddtoPlaylist  countAddFriend  \
0           2              7                   9              12   
1          12             11                  61              49   
2           0              1                   3               2   
3           0              0                   5               1   
4           0              0                   2               0   

   countNextSong  countThumbsUp  countHelp  countUpgrade  countError  \
0            673             37          1             0           0   
1           2682            148         18             1           3   
2            133              8          1             2           1   
3            195              5          0             0           0   
4             51              3          1             0           0   

   countSubmitUpgrade  
0                   0  
1                   1  
2                   0  
3                   0  
4                   0

In [93]:
pg_counts = pd_temp['pageCount'].values
user_ids = pd_temp['userId'].values

pd_temp_t = pd_temp.transpose().iloc[2:,:]
pd_temp_t.head()

0    1   2   3   4   5   6   7   8   9   ... 215 216  \
countSubmitDowngrade   0    1   0   0   0   2   0   0   0   1 ...   0   0   
countThumbsDown        4   27   2   0   0  11   3   2   6   6 ...   0  24   
countHome             30  105  11   6   7  66  15   2  20  24 ...   2  90   
countDowngrade         7   30   0   2   0  10   0   0   7  10 ...   0  22   
countRollAdvert        1   25  14   3   9  86  18   3   5  20 ...   3   5   

                      217 218 219 220 221  222  223 224  
countSubmitDowngrade    1   0   0   1   1    0    0   0  
countThumbsDown        72   4   1  25  24   12   22   5  
countHome             266  31  12  67  71  100  115  24  
countDowngrade         68   3   0  15  20   17   25   2  
countRollAdvert        85  43  12  50  17   24   30  10  

[5 rows x 225 columns]

In [94]:
len(pg_counts)

225

In [95]:
pd_temp_t.shape

(17, 225)

In [96]:
# calculate percentage from page views
for i in range(pd_temp_t.shape[1]):
    pd_temp_t[pd_temp_t.columns[i]] = 100 * pd_temp_t[pd_temp_t.columns[i]] \
                                                      / pg_counts[i]
    
pd_temp_t.head()

0          1        2         3        4    \
countSubmitDowngrade         0  0.0311139        0         0        0   
countThumbsDown       0.503145   0.840075  1.06952         0        0   
countHome              3.77358    3.26696  5.88235   2.75229  8.97436   
countDowngrade        0.880503   0.933416        0  0.917431        0   
countRollAdvert       0.125786   0.777847  7.48663   1.37615  11.5385   

                           5        6        7         8         9    \
countSubmitDowngrade  0.160643        0        0         0  0.106383   
countThumbsDown       0.883534  1.38889  4.54545   1.15385  0.638298   
countHome               5.3012  6.94444  4.54545   3.84615   2.55319   
countDowngrade        0.803213        0        0   1.34615   1.06383   
countRollAdvert        6.90763  8.33333  6.81818  0.961538   2.12766   

                        ...         215       216        217       218  \
countSubmitDowngrade    ...           0         0  0.0138313         0   
countThumbsDown         ...           0  0.796284   0.995851  0.490798   
countHome               ...     4.44444   2.98607    3.67911   3.80368   
countDowngrade          ...           0  0.729927   0.940526  0.368098   
countRollAdvert         ...     6.66667  0.165893    1.17566   5.27607   

                           219       220        221       222       223  \
countSubmitDowngrade         0  0.047824  0.0459559         0         0   
countThumbsDown       0.534759    1.1956    1.10294  0.499168  0.760982   
countHome              6.41711   3.20421    3.26287   4.15973   3.97786   
countDowngrade               0   0.71736   0.919118  0.707155  0.864753   
countRollAdvert        6.41711    2.3912    0.78125  0.998336    1.0377   

                           224  
countSubmitDowngrade         0  
countThumbsDown       0.814332  
countHome              3.90879  
countDowngrade        0.325733  
countRollAdvert        1.62866  

[5 rows x 225 columns]

In [97]:
pd_temp = pd_temp_t.transpose()
pd_temp.head()

countSubmitDowngrade countThumbsDown countHome countDowngrade  \
0                    0        0.503145   3.77358       0.880503   
1            0.0311139        0.840075   3.26696       0.933416   
2                    0         1.06952   5.88235              0   
3                    0               0   2.75229       0.917431   
4                    0               0   8.97436              0   

  countRollAdvert countLogout countSaveSettings countAbout countSettings  \
0        0.125786     1.38365          0.125786   0.251572      0.880503   
1        0.777847     1.08899          0.155569   0.373367      0.342253   
2         7.48663     3.74332                 0          0      0.534759   
3         1.37615    0.458716                 0          0             0   
4         11.5385     3.84615                 0          0             0   

  countAddtoPlaylist countAddFriend countNextSong countThumbsUp countHelp  \
0            1.13208        1.50943       84.6541       4.65409  0.125786   
1            1.89795        1.52458       83.4474       4.60485   0.56005   
2            1.60428        1.06952        71.123       4.27807  0.534759   
3            2.29358       0.458716       89.4495       2.29358         0   
4             2.5641              0       65.3846       3.84615   1.28205   

  countUpgrade countError countSubmitUpgrade  
0            0          0                  0  
1    0.0311139  0.0933416          0.0311139  
2      1.06952   0.534759                  0  
3            0          0                  0  
4            0          0                  0

In [98]:
pd_temp = pd_temp.rename(columns = lambda col_name: col_name.replace("count", "p"))
pd_temp['userId'] = user_ids
pd_temp.head()

pSubmitDowngrade pThumbsDown    pHome pDowngrade pRollAdvert   pLogout  \
0                0    0.503145  3.77358   0.880503    0.125786   1.38365   
1        0.0311139    0.840075  3.26696   0.933416    0.777847   1.08899   
2                0     1.06952  5.88235          0     7.48663   3.74332   
3                0           0  2.75229   0.917431     1.37615  0.458716   
4                0           0  8.97436          0     11.5385   3.84615   

  pSaveSettings    pAbout pSettings pAddtoPlaylist pAddFriend pNextSong  \
0      0.125786  0.251572  0.880503        1.13208    1.50943   84.6541   
1      0.155569  0.373367  0.342253        1.89795    1.52458   83.4474   
2             0         0  0.534759        1.60428    1.06952    71.123   
3             0         0         0        2.29358   0.458716   89.4495   
4             0         0         0         2.5641          0   65.3846   

  pThumbsUp     pHelp   pUpgrade     pError pSubmitUpgrade  userId  
0   4.65409  0.125786          0          0              0      10  
1   4.60485   0.56005  0.0311139  0.0933416      0.0311139     100  
2   4.27807  0.534759    1.06952   0.534759              0  100001  
3   2.29358         0          0          0              0  100002  
4   3.84615   1.28205          0          0              0  100003

In [99]:
reordered = [pd_temp.columns[-1]] + list(pd_temp.columns[:-1])
reordered

['userId',
 'pSubmitDowngrade',
 'pThumbsDown',
 'pHome',
 'pDowngrade',
 'pRollAdvert',
 'pLogout',
 'pSaveSettings',
 'pAbout',
 'pSettings',
 'pAddtoPlaylist',
 'pAddFriend',
 'pNextSong',
 'pThumbsUp',
 'pHelp',
 'pUpgrade',
 'pError',
 'pSubmitUpgrade']

In [100]:
pd_temp = pd_temp[reordered]
pd_temp.head()

userId pSubmitDowngrade pThumbsDown    pHome pDowngrade pRollAdvert  \
0      10                0    0.503145  3.77358   0.880503    0.125786   
1     100        0.0311139    0.840075  3.26696   0.933416    0.777847   
2  100001                0     1.06952  5.88235          0     7.48663   
3  100002                0           0  2.75229   0.917431     1.37615   
4  100003                0           0  8.97436          0     11.5385   

    pLogout pSaveSettings    pAbout pSettings pAddtoPlaylist pAddFriend  \
0   1.38365      0.125786  0.251572  0.880503        1.13208    1.50943   
1   1.08899      0.155569  0.373367  0.342253        1.89795    1.52458   
2   3.74332             0         0  0.534759        1.60428    1.06952   
3  0.458716             0         0         0        2.29358   0.458716   
4   3.84615             0         0         0         2.5641          0   

  pNextSong pThumbsUp     pHelp   pUpgrade     pError pSubmitUpgrade  
0   84.6541   4.65409  0.125786          0          0              0  
1   83.4474   4.60485   0.56005  0.0311139  0.0933416      0.0311139  
2    71.123   4.27807  0.534759    1.06952   0.534759              0  
3   89.4495   2.29358         0          0          0              0  
4   65.3846   3.84615   1.28205          0          0              0

In [101]:
page_prop_spark = spark.createDataFrame(pd_temp)
page_prop_spark.show(5)

+------+--------------------+------------------+------------------+------------------+-------------------+-------------------+-------------------+-------------------+------------------+------------------+-------------------+-----------------+------------------+-------------------+--------------------+-------------------+--------------------+
|userId|    pSubmitDowngrade|       pThumbsDown|             pHome|        pDowngrade|        pRollAdvert|            pLogout|      pSaveSettings|             pAbout|         pSettings|    pAddtoPlaylist|         pAddFriend|        pNextSong|         pThumbsUp|              pHelp|            pUpgrade|             pError|      pSubmitUpgrade|
+------+--------------------+------------------+------------------+------------------+-------------------+-------------------+-------------------+-------------------+------------------+------------------+-------------------+-----------------+------------------+-------------------+--------------------+----------

In [102]:
h.spark_shape(page_prop_spark)

(225, 18)

### 8. Number of artists user has listened to

In [103]:
artist_df = df_c.filter(df.page == "NextSong") \
                 .select("userId", "artist") \
                 .dropDuplicates() \
                 .groupBy("userId") \
                 .count() \
                 .orderBy("userId")

artist_df = artist_df.withColumnRenamed("count", "artistCount")

artist_df.show(5)

+------+-----------+
|userId|artistCount|
+------+-----------+
|    10|        565|
|   100|       1705|
|100001|        125|
|100002|        184|
|100003|         50|
+------+-----------+
only showing top 5 rows



In [104]:
h.spark_shape(artist_df)

(225, 2)

### 9. Region based on midwest, northeast, south and west

In [105]:
# get state from location column
get_state = udf(lambda location: location.split(", ")[-1])
df_c = df_c.withColumn("state", get_state(df_c.location))

# view
df_c.select("state").show(5)

+-----+
|state|
+-----+
|   CA|
|MA-NH|
|   CA|
|MA-NH|
|   CA|
+-----+
only showing top 5 rows



In [106]:
midwest = sorted(["IL-MO", "OH", "MN-WI", "KY-IN", "NE-IA", "IL-IN-WI", \
                  "MI", "MO-KS", "IN", "WI", "IA", "MO-IL", "OH-KY-IN", "IL"])

northeast = sorted(["MA-NH", "NY-NJ-PA", "PA-NJ-DE-MD", "CT", "NJ", "PA-NJ", \
                    "NH", "PA", "NY", "RI-MA"])

south = sorted(["FL", "MD", "TX", "GA-AL", "GA", "TN-VA", "SC-NC", "WV", \
                "OK", "KY", "VA-NC", "NC-SC", "MS", "VA", "AL", \
                "DC-VA-MD-WV", "TN-MS-AR", "LA", "AR", "SC", "NC", "MD-WV", \
                "TN"])

west = sorted(["CA", "WA", "CO", "AZ", "UT", "NV", "MT", "AK", "OR", \
               "UT-ID", "OR-WA"])

In [107]:
# get region from state column
get_region = udf(lambda state: "midwest" if state in midwest \
                 else "northeast" if state in northeast \
                 else "west" if state in west \
                 else "south")

# create region column
df_c = df_c.withColumn("region", get_region(df_c.state))

# drop extra columns now: location and state
df_c = df_c.drop("location", "state")

Verifying:

In [108]:
for col in ["location", "state"]:
    if col not in df_c.columns:
        print("{0} column removed".format(col))

location column removed
state column removed


Creating dummy variables for region column.

In [109]:
# mapping
regions = df_c.select("region") \
            .distinct() \
            .rdd \
            .flatMap(lambda region: region) \
            .collect()

# expression for naming pattern
regions_expr = [Fwhen(Fcol("region") == region, 1) \
                 .otherwise(0) \
                 .alias("region" + region.capitalize()) \
                 for region in regions]

# adding new column and droppings old ones
region_df = df_c.select("userId", "region", *regions_expr) \
                .dropDuplicates() \
                .orderBy("userId") \
                .drop("region")

# view
region_df.show(5)

+------+---------------+-------------+----------+-----------+
|userId|regionNortheast|regionMidwest|regionWest|regionSouth|
+------+---------------+-------------+----------+-----------+
|    10|              0|            0|         0|          1|
|   100|              0|            0|         0|          1|
|100001|              0|            0|         0|          1|
|100002|              0|            0|         1|          0|
|100003|              0|            0|         0|          1|
+------+---------------+-------------+----------+-----------+
only showing top 5 rows



In [110]:
h.spark_shape(region_df)

(225, 5)

### 10. Churn

In [111]:
# getting on ly churn column
churn_df = df_c.select("userId", "isChurn") \
               .dropDuplicates() \
               .orderBy("userId")

# changing data type to int
churn_df = churn_df.select("userId", churn_df["isChurn"].cast("int"))

churn_df.persist()

DataFrame[userId: string, isChurn: int]

In [112]:
churn_df.show(5)

+------+-------+
|userId|isChurn|
+------+-------+
|    10|      0|
|   100|      0|
|100001|      1|
|100002|      0|
|100003|      1|
+------+-------+
only showing top 5 rows



In [113]:
h.spark_shape(churn_df)

(225, 2)

Now, let's create a dataframe containing all the new features.

In [114]:
# engineered features
engd_features = [gender_df, song_df, session_df, avg_songs_per_session_df, \
                 avg_time_per_session_df, recent_level_df, page_prop_spark, \
                 artist_df, region_df, churn_df]

# master dataframe to merge new features with
# this will initially contain only distinct user IDs
# then we'll the engineered features
master = df_c.select("userID").dropDuplicates()

master.show(5)

+------+
|userID|
+------+
|100010|
|200002|
|   125|
|    51|
|   124|
+------+
only showing top 5 rows



In [115]:
for f in engd_features:
    # rename userId temporarily so that it does not clash with userId of master
    f = f.withColumnRenamed("userId", "userIdDrop")
    # merged engineered features on userId and then drop the temporary userId \
    # created from engineered features dataframe
    master = master.join(f, on = master["userId"] == f["userIdDrop"], how = 'left').drop("userIdDrop")

# view
master.show(5)

+------+-------+-------+---------+------------+------------------+-------------------------+---------+---------+----------------+------------------+------------------+------------------+-------------------+------------------+--------------------+-------------------+-------------------+------------------+------------------+-----------------+------------------+-------------------+------------------+--------------------+------------------+-----------+---------------+-------------+----------+-----------+-------+
|userID|genderF|genderM|songCount|sessionCount|avgSongsPerSession|avgSessionDurationMinutes|levelFree|levelPaid|pSubmitDowngrade|       pThumbsDown|             pHome|        pDowngrade|        pRollAdvert|           pLogout|       pSaveSettings|             pAbout|          pSettings|    pAddtoPlaylist|        pAddFriend|        pNextSong|         pThumbsUp|              pHelp|          pUpgrade|              pError|    pSubmitUpgrade|artistCount|regionNortheast|regionMidwest|regi

In [116]:
# dimension of data
h.spark_shape(master)

(225, 32)

Save processed data.

In [117]:
# master.repartition(1).write.format("csv").option("header", "true") \
#       .save("cleaned_data")

In [118]:
master.persist()

DataFrame[userID: string, genderF: int, genderM: int, songCount: bigint, sessionCount: bigint, avgSongsPerSession: double, avgSessionDurationMinutes: double, levelFree: int, levelPaid: int, pSubmitDowngrade: double, pThumbsDown: double, pHome: double, pDowngrade: double, pRollAdvert: double, pLogout: double, pSaveSettings: double, pAbout: double, pSettings: double, pAddtoPlaylist: double, pAddFriend: double, pNextSong: double, pThumbsUp: double, pHelp: double, pUpgrade: double, pError: double, pSubmitUpgrade: double, artistCount: bigint, regionNortheast: int, regionMidwest: int, regionWest: int, regionSouth: int, isChurn: int]

<a id="model"></a>

# Modelling

Split the full dataset into train, test, and validation sets. Test out several of the machine learning methods you learned. Evaluate the accuracy of the various models, tuning parameters as necessary. Determine your winning model based on test accuracy and report results on the validation set. Since the churned users are a fairly small subset, I suggest using F1 score as the metric to optimize.

First and foremost, the class distribution.

In [154]:
master.groupBy("isChurn").count().show()

+-------+-----+
|isChurn|count|
+-------+-----+
|      1|   52|
|      0|  173|
+-------+-----+



We will first see the results without undersampling.

In [155]:
master_c_pd = master.groupBy("isChurn").count().toPandas()

In [156]:
h.churn_dist(master_c_pd)

In [157]:
# create feature space
assembler = VectorAssembler(inputCols = master.columns[1:-1],
                            outputCol = "FeaturesVec")

data = assembler.transform(master)
# data.show(5)

In [158]:
# standardise
scaler = StandardScaler(inputCol = "FeaturesVec",
                        outputCol = "FeaturesScaled",
                        withStd = True)
scaler = scaler.fit(data)
data = scaler.transform(data)
# data.show(5)

In [159]:
# select transformed columns for training and testing splits
data = data.select(data.isChurn.alias("label"),
                   data.FeaturesScaled.alias("features"))

In [160]:
# train-test splits
training, test = data.randomSplit([0.8, 0.2],
                              seed = 42)

training.cache()

DataFrame[label: int, features: vector]

In [311]:
training.groupby("label") \
        .count() \
        .show()

+-----+-----+
|label|count|
+-----+-----+
|    1|   42|
|    0|  149|
+-----+-----+



In [161]:
print((time.time() - st)/60)

7.483675905068716


The most common classification algorithms are available in PySpark API. Some of them which we'll be using are:
1. [Logistic Regression](https://spark.apache.org/docs/2.1.1/ml-classification-regression.html#logistic-regression)
2. [Random Forest](https://spark.apache.org/docs/2.1.1/ml-classification-regression.html#random-forest-classifier)
3. [Gradient Boosted Trees](https://spark.apache.org/docs/2.2.0/ml-classification-regression.html#gradient-boosted-trees-gbts)

1. Logistic Regression

In [162]:
# instantiate model
lr = LogisticRegression()

In [163]:
# grid-search
paramGrid = ParamGridBuilder() \
                .addGrid(lr.elasticNetParam, [0.0, 0.4, 0.8]) \
                .addGrid(lr.regParam, [0.0, 0.8]) \
                .addGrid(lr.maxIter, [10]) \
                .build()

In [164]:
# cross-validation
cv = CrossValidator(estimator = lr,
                           estimatorParamMaps = paramGrid,
                           evaluator = MulticlassClassificationEvaluator(),
                           numFolds = 3)

In [165]:
# train
lrModel = cv.fit(training)

In [166]:
# save model 
lrModel.save("lrModel")

In [167]:
# evaluate
lrModel.avgMetrics

[0.7171729824551215,
 0.6818064374878903,
 0.7171729824551215,
 0.6843741312320546,
 0.7171729824551215,
 0.6843741312320546]

2. Random Forest Classifier

In [168]:
# instantiate model
rf = RandomForestClassifier()

In [169]:
# grid-search
paramGrid = ParamGridBuilder() \
            .addGrid(rf.impurity,['entropy', 'gini']) \
            .addGrid(rf.maxDepth,[5, 10]) \
            .addGrid(rf.seed, [42]) \
            .build()

In [170]:
# cross-validation
cv = CrossValidator(estimator=rf,
                    estimatorParamMaps=paramGrid,
                    evaluator=MulticlassClassificationEvaluator(),
                    numFolds=3)

In [171]:
# train
rfModel = cv.fit(training)

In [172]:
# save model
rfModel.save("rfModel")

In [173]:
# evaluate
rfModel.avgMetrics

[0.7100662848177904,
 0.6977767827116292,
 0.6998464783535147,
 0.6934705695275152]

3. GBT Classifier

In [174]:
# instantiate model
gbt = GBTClassifier()

In [175]:
# grid-search
paramGrid = ParamGridBuilder() \
    .addGrid(gbt.maxIter,[3, 10]) \
    .addGrid(gbt.maxDepth,[4, 8]) \
    .build()

In [176]:
# cross-validation
cv = CrossValidator(estimator=gbt,
                          estimatorParamMaps=paramGrid,
                          evaluator=MulticlassClassificationEvaluator(),
                          numFolds=3)

In [177]:
# train
gbtModel = cv.fit(training)

In [178]:
# save model
gbtModel.save("gbtModel")

In [179]:
# evaluate
gbtModel.avgMetrics

[0.7088223698939935,
 0.6840626422234756,
 0.7050420005070258,
 0.6836625808413633]

Random undersampling to handle imbalance

In [180]:
# perform resampling
resampled_training = training.sampleBy("label", fractions={0: 52/225,\
                                                           1: 1.0}) \
                             .cache()

# view resampled data
resampled_training.groupby("label") \
                  .count() \
                  .show()

+-----+-----+
|label|count|
+-----+-----+
|    1|   42|
|    0|   43|
+-----+-----+



Now fitting the models again on undersampled data.
1. Logistic Regression

In [181]:
# instantiate model
new_lr = LogisticRegression()

In [182]:
# grid-search
paramGrid = ParamGridBuilder() \
                .addGrid(new_lr.elasticNetParam, [0.0, 0.4, 0.8]) \
                .addGrid(new_lr.regParam, [0.0, 0.8]) \
                .addGrid(new_lr.maxIter, [10]) \
                .build()

In [183]:
# cross-validation
cv = CrossValidator(estimator = new_lr,
                    estimatorParamMaps = paramGrid,
                    evaluator = MulticlassClassificationEvaluator(),
                    numFolds = 3)

In [184]:
# train
new_lr_model = cv.fit(resampled_training)

In [185]:
# save model
new_lr_model.save("new_lr_model")

In [188]:
# evaluate
new_lr_model.avgMetrics

[0.4862929285145422,
 0.3439232644534371,
 0.4862929285145422,
 0.1922010923735343,
 0.4862929285145422,
 0.1922010923735343]

2. Random Forest Classifier

In [189]:
# instantiate model
new_rf = RandomForestClassifier()

In [190]:
# grid-search
paramGrid = ParamGridBuilder() \
            .addGrid(new_rf.impurity,['entropy', 'gini']) \
            .addGrid(new_rf.maxDepth,[5, 10]) \
            .addGrid(new_rf.seed, [42]).build()

In [191]:
# cross-validation
cv = CrossValidator(estimator=new_rf,
                    estimatorParamMaps=paramGrid,
                    evaluator=MulticlassClassificationEvaluator(),
                    numFolds=3)

In [192]:
# train
new_rf_model = cv.fit(resampled_training)

In [193]:
# save model
new_rf_model.save("new_rf_model")

In [194]:
# evaluate
new_rf_model.avgMetrics

[0.5366478432119142,
 0.5316646065389341,
 0.539935866917964,
 0.49981264969756023]

3. GBT Classifier

In [195]:
# instantiate model
new_gbt = GBTClassifier()

In [196]:
# grid-search
paramGrid = ParamGridBuilder() \
                .addGrid(new_gbt.maxIter,[3, 10]) \
                .addGrid(new_gbt.maxDepth,[4, 8]) \
                .build()

In [197]:
# cross-validation
cv = CrossValidator(estimator=new_gbt,
                    estimatorParamMaps=paramGrid,
                    evaluator=MulticlassClassificationEvaluator(),
                    numFolds=3)

In [198]:
# train
new_gbt_model = cv.fit(resampled_training)

In [199]:
# save model
new_gbt_model.save('new_gbt_model')

In [200]:
# evaluate
new_gbt_model.avgMetrics

[0.6274144650080521,
 0.6287962580992537,
 0.6161026605927994,
 0.6287962580992537]

In [201]:
print((time.time()-st)/60)

67.07211228609086


#### Using the validation data to evaluate the best model through F1 score.

Score before under-sampling

In [215]:
results = gbtModel.transform(test)

In [217]:
tp = results.filter("label = 1 and prediction = 1").count()
fp = results.filter("label = 0 and prediction = 1").count()
fn = results.filter("label = 1 and prediction = 0").count()
precision = tp / (tp + fp) 
recall = tp / (tp + fn)
f1 = 2*precision*recall / (precision+recall)
print(precision)
print(recall)
print(f1)

0.5714285714285714
0.4
0.47058823529411764


Score after under-sampling

In [218]:
results = new_gbt_model.transform(test)

In [219]:
tp = results.filter("label = 1 and prediction = 1").count()
fp = results.filter("label = 0 and prediction = 1").count()
fn = results.filter("label = 1 and prediction = 0").count()
precision = tp / (tp + fp) 
recall = tp / (tp + fn)
f1 = 2 * precision * recall / (precision + recall)
print(precision)
print(recall)
print(f1)

0.5333333333333333
0.8
0.64


Getting feature importance:

In [234]:
feat_imp = new_gbt_model.bestModel.featureImportances
feat_imp

SparseVector(30, {0: 0.0418, 3: 0.1429, 8: 0.0733, 9: 0.1908, 10: 0.0687, 12: 0.0134, 14: 0.0447, 15: 0.1136, 16: 0.0992, 17: 0.0087, 18: 0.0044, 21: 0.0928, 22: 0.0164, 25: 0.0772, 29: 0.012})

In [241]:
feat_imp.indices

array([ 0,  3,  8,  9, 10, 12, 14, 15, 16, 17, 18, 21, 22, 25, 29],
      dtype=int32)

In [243]:
for i in feat_imp.indices:
    print(feat_imp[int(i)])

0.0418358557893442
0.14287691820914408
0.07333159949439022
0.19075464341245074
0.06873033451106537
0.01344723936086064
0.0447120708748616
0.11362917259927231
0.09915758240308585
0.008715803289446702
0.004357901644723367
0.0928323213808378
0.016435514774385183
0.07722994060203359
0.011953101654098347


In [244]:
feature_importance = {}
for i in feat_imp.indices:
    feature_importance[int(i)]= feat_imp[int(i)]

In [245]:
feature_importance

{0: 0.0418358557893442,
 3: 0.14287691820914408,
 8: 0.07333159949439022,
 9: 0.19075464341245074,
 10: 0.06873033451106537,
 12: 0.01344723936086064,
 14: 0.0447120708748616,
 15: 0.11362917259927231,
 16: 0.09915758240308585,
 17: 0.008715803289446702,
 18: 0.004357901644723367,
 21: 0.0928323213808378,
 22: 0.016435514774385183,
 25: 0.07722994060203359,
 29: 0.011953101654098347}

In [308]:
import operator
# x = {1: 2, 3: 4, 4: 3, 2: 1, 0: 0}
sorted_x = dict(sorted(feature_importance.items(), key=operator.itemgetter(1), reverse = True))
# from pprint import pprint
# print(dict(sorted_x))

In [309]:
sorted_x

{9: 0.19075464341245074,
 3: 0.14287691820914408,
 15: 0.11362917259927231,
 16: 0.09915758240308585,
 21: 0.0928323213808378,
 25: 0.07722994060203359,
 8: 0.07333159949439022,
 10: 0.06873033451106537,
 14: 0.0447120708748616,
 0: 0.0418358557893442,
 22: 0.016435514774385183,
 12: 0.01344723936086064,
 29: 0.011953101654098347,
 17: 0.008715803289446702,
 18: 0.004357901644723367}

In [303]:
old_keys = list(sorted_x.keys())
old_keys

[9, 3, 15, 16, 21, 25, 8, 10, 14, 0, 22, 12, 29, 17, 18]

In [304]:
for new_key, old_key in zip(new_keys, old_keys):
    print(new_key, old_key)

pSubmitDowngrade 9
songCount 3
pSaveSettings 15
pAbout 16
pThumbsUp 21
pSubmitUpgrade 25
levelPaid 8
pThumbsDown 10
pLogout 14
userID 0
pHelp 22
pDowngrade 12
regionWest 29
pSettings 17
pAddtoPlaylist 18


In [305]:
for i, j in zip(range(len(new_keys)), range(len(old_keys))):
#     print(new_key, old_key)
    new_key = new_keys[i]
    old_key = old_keys[i]
    sorted_x[new_key] = sorted_x[old_key]
    del sorted_x[old_key]
    i += 1
    j += 1

In [306]:
sorted_x

{'pSubmitDowngrade': 0.19075464341245074,
 'songCount': 0.14287691820914408,
 'pSaveSettings': 0.11362917259927231,
 'pAbout': 0.09915758240308585,
 'pThumbsUp': 0.0928323213808378,
 'pSubmitUpgrade': 0.07722994060203359,
 'levelPaid': 0.07333159949439022,
 'pThumbsDown': 0.06873033451106537,
 'pLogout': 0.0447120708748616,
 'userID': 0.0418358557893442,
 'pHelp': 0.016435514774385183,
 'pDowngrade': 0.01344723936086064,
 'regionWest': 0.011953101654098347,
 'pSettings': 0.008715803289446702,
 'pAddtoPlaylist': 0.004357901644723367}

These are the feature sorted in decreasing order of relevance while training. `pSubmitDowngrade` is highest because it is somewhat similar to to churn.

<a id="conclusion"></a>

## Conclusion

I enjoyed the data pre-processing part of the project. For data visualisation part, instead of using “for” loops to get arrays for our bar chart, I first converted our Spark data frame to Pandas data frame using `toPandas()` method. Data visualisation is easier from then on.

The shape of our final data is just 225 x 32. This is too small to generalise our model. Just 225 users for a streaming company? That’s nothing. 12 GB data might provide some useful results. If you want more statistically significant results then I suggest you run this notebook on Amazon EMR for the 12 GB dataset. I have skipped that part for now because it costs $30 for one week.

Some of the challenges which I faced in this project are:

- Official documentation of PySpark as compared to Pandas
- For the sake of mastering Spark, we only used the most common machine learning classification models instead of using the advanced ones
- Highly imbalanced data led to a poor F1 score
- If you run this notebook without any changes, then it will take around an **hour** to run completely